#  Import

In [1]:
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
import tensorflow as tf
import keras
import math
import datetime, os
from keras.callbacks import EarlyStopping
from sklearn import preprocessing
from sklearn.preprocessing import MinMaxScaler
import itertools
from functions.common_function import *
from functions.initialize_model import initialize_model_expanded
from functions.cross_validation import cross_validation_split
from functions.dataset_interpolation import dataset_interpolation_sklearn
from scipy.stats import pearsonr

'''Enabling plotting of graphs just below the plotting commands'''
%matplotlib inline
'''Enabling the disply of all rows and columns within the dataframe'''
pd.set_option("display.max_rows", None, "display.max_columns", None)

#  Constant

In [2]:
num_feature = 8
cat_col = [4, 5]
num_ori_feature = num_feature - len(cat_col)
num_target = 3
bandwidth = 100
num_epochs = 10000
num_batch = 10
num_folds = 4
directory_name = "Counter_Choudhury_Method_SKLearn_Gaussian_Kernel"

limit = pd.DataFrame({'lower' : [303, 20, 0, 2, 6, 1.5, 122, 1236, 14], \
                     'higher' : [840, 44, 17, 5, 8, 2, 408, 3240, 101], \
                     'ref' : [530, 40, 14, 3.2, 6, 1.8, np.nan, np.nan, np.nan]})

'''Import dataset'''
dataset = pd.read_csv("Dataset/Choudhury_Dataset.csv")

#  Implementation

In [3]:
'''Iterate 10 times to mimic Cross Validation'''
MAE = []
MSE = []
RMSE = []

folds = cross_validation_split(dataset, num_folds)


'''Cross Validation'''
for i in range(len(folds)):
    test_index = [folds[i]]
    train_index = [fold for fold in folds if fold not in test_index]
    test_index = list(itertools.chain.from_iterable(test_index))
    train_index = list(itertools.chain.from_iterable(train_index))
    
    '''Dataset Interpolation'''
    interpolated_dataset = dataset_interpolation_sklearn(dataset.iloc[train_index], num_ori_feature, num_target, limit)
    
    '''Converting Categorical Data into binary representation'''
    converted_dataset = convert_cat(interpolated_dataset, cat_col, num_ori_feature, num_target, [interpolated_dataset.iloc[:, 4].unique(), interpolated_dataset.iloc[:, 5].unique()])
    converted_test_dataset = convert_cat(dataset.iloc[test_index], cat_col, num_ori_feature, num_target, [dataset.iloc[:, 4].unique(), dataset.iloc[:, 5].unique()])
    
    '''Normalising dataset using Min Max present in the train set'''
    scaler = MinMaxScaler()
    scaler.fit(converted_dataset)
    
    '''Normalising of train and test set'''
    normalised_train_dataset = pd.DataFrame(scaler.transform(converted_dataset), columns = get_col_names(converted_dataset))
    normalised_test_dataset = pd.DataFrame(scaler.transform(converted_test_dataset), columns = get_col_names(converted_dataset))
    
    x_train = normalised_train_dataset.iloc[:, 0: num_feature]
    y_train =  normalised_train_dataset.iloc[:, num_feature: num_feature + num_target]
    x_test = normalised_test_dataset.iloc[:, 0: num_feature]
    y_test = normalised_test_dataset.iloc[:, num_feature: num_feature + num_target]
    
    model = initialize_model_expanded(num_feature, num_target, 'relu')
    
    '''Model Fitting'''
    print('------------------------------------------------------------------------')
    print(f'Training for fold {i + 1} ...')
    '''Initializing early stopping that prevents overfitting 
    and tensorboard for visualizing machine learning workflow'''
    early_stopping = EarlyStopping(monitor = 'loss', mode = 'min', verbose = 1, patience = 1800)
    logdir = os.path.join(f"logs/{directory_name}", "ANN_" + str(i + 1))
    tensorboard_callback = tf.keras.callbacks.TensorBoard(logdir, \
                                                         histogram_freq = 1,
                                                         write_graph = True,\
                                                         write_images = True)
    
    history = model.fit(x_train,\
                        y_train,
                        epochs = num_epochs,\
                        batch_size = num_batch,\
                        callbacks = [tensorboard_callback, early_stopping])

    '''Index 0 of result is represented by Mean Absolute Error'''
    result = model.evaluate(x_test, y_test, batch_size = 128)
    MAE.append(result[0])
    MSE.append(result[1])
    RMSE.append(result[2])
    model.save(f"Model\{directory_name}\model_{i + 1}")
    print("Saved model to disk")    
    print(f'Score for fold {i + 1}: {model.metrics_names[0]} of {result[0]}')
    
'''Provide average score'''
print('------------------------------------------------------------------------')
print('Score per fold')
for i in range(0, len(MAE)):
    print('------------------------------------------------------------------------')
    print(f'> Iteration {i+1} - MAE: {MAE[i]} - MSE: {MSE[i]}- RMSE: {RMSE[i]}') 
print('------------------------------------------------------------------------')
print('Average scores for all folds:')
print(f'> MAE: {np.mean(MAE)} - Standard Deviation: {np.std(MAE)}')
print(f'> MSE: {np.mean(MSE)}')
print(f'> RMSE: {np.mean(RMSE)}')
print('------------------------------------------------------------------------')   

------------------------------------------------------------------------
Training for fold 1 ...
Epoch 1/10000
 1/59 [..............................] - ETA: 0s - loss: 0.3440 - mean_squared_error: 0.1590 - root_mean_squared_error: 0.3987WARNING:tensorflow:From C:\Users\hfyyl2\.conda\envs\liew_new\lib\site-packages\tensorflow\python\ops\summary_ops_v2.py:1277: stop (from tensorflow.python.eager.profiler) is deprecated and will be removed after 2020-07-01.
Instructions for updating:
use `tf.profiler.experimental.stop` instead.
59/59 [==============================] - 0s 2ms/step - loss: 0.2846 - mean_squared_error: 0.1152 - root_mean_squared_error: 0.3394
Epoch 2/10000
59/59 [==============================] - 0s 984us/step - loss: 0.1705 - mean_squared_error: 0.0445 - root_mean_squared_error: 0.2108
Epoch 3/10000
59/59 [==============================] - 0s 978us/step - loss: 0.1457 - mean_squared_error: 0.0337 - root_mean_squared_error: 0.1835
Epoch 4/10000
59/59 [=======================

59/59 [==============================] - 0s 1ms/step - loss: 0.0240 - mean_squared_error: 0.0035 - root_mean_squared_error: 0.0590
Epoch 52/10000
59/59 [==============================] - 0s 976us/step - loss: 0.0234 - mean_squared_error: 0.0034 - root_mean_squared_error: 0.0583
Epoch 53/10000
59/59 [==============================] - 0s 933us/step - loss: 0.0232 - mean_squared_error: 0.0034 - root_mean_squared_error: 0.0584
Epoch 54/10000
59/59 [==============================] - 0s 964us/step - loss: 0.0239 - mean_squared_error: 0.0035 - root_mean_squared_error: 0.0589
Epoch 55/10000
59/59 [==============================] - 0s 975us/step - loss: 0.0235 - mean_squared_error: 0.0035 - root_mean_squared_error: 0.0588
Epoch 56/10000
59/59 [==============================] - 0s 938us/step - loss: 0.0240 - mean_squared_error: 0.0034 - root_mean_squared_error: 0.0587
Epoch 57/10000
59/59 [==============================] - 0s 964us/step - loss: 0.0245 - mean_squared_error: 0.0035 - root_mean_squ

59/59 [==============================] - 0s 908us/step - loss: 0.0213 - mean_squared_error: 0.0032 - root_mean_squared_error: 0.0563
Epoch 106/10000
59/59 [==============================] - 0s 967us/step - loss: 0.0216 - mean_squared_error: 0.0032 - root_mean_squared_error: 0.0569
Epoch 107/10000
59/59 [==============================] - 0s 898us/step - loss: 0.0208 - mean_squared_error: 0.0032 - root_mean_squared_error: 0.0568
Epoch 108/10000
59/59 [==============================] - 0s 933us/step - loss: 0.0215 - mean_squared_error: 0.0033 - root_mean_squared_error: 0.0570
Epoch 109/10000
59/59 [==============================] - 0s 891us/step - loss: 0.0207 - mean_squared_error: 0.0032 - root_mean_squared_error: 0.0563
Epoch 110/10000
59/59 [==============================] - 0s 899us/step - loss: 0.0211 - mean_squared_error: 0.0032 - root_mean_squared_error: 0.0564
Epoch 111/10000
59/59 [==============================] - 0s 901us/step - loss: 0.0215 - mean_squared_error: 0.0032 - root_

59/59 [==============================] - 0s 967us/step - loss: 0.0188 - mean_squared_error: 0.0030 - root_mean_squared_error: 0.0550
Epoch 161/10000
59/59 [==============================] - 0s 927us/step - loss: 0.0188 - mean_squared_error: 0.0030 - root_mean_squared_error: 0.0552
Epoch 162/10000
59/59 [==============================] - 0s 950us/step - loss: 0.0189 - mean_squared_error: 0.0030 - root_mean_squared_error: 0.0549
Epoch 163/10000
59/59 [==============================] - 0s 951us/step - loss: 0.0198 - mean_squared_error: 0.0031 - root_mean_squared_error: 0.0555
Epoch 164/10000
59/59 [==============================] - 0s 959us/step - loss: 0.0201 - mean_squared_error: 0.0031 - root_mean_squared_error: 0.0554
Epoch 165/10000
59/59 [==============================] - 0s 984us/step - loss: 0.0192 - mean_squared_error: 0.0031 - root_mean_squared_error: 0.0553
Epoch 166/10000
59/59 [==============================] - 0s 929us/step - loss: 0.0191 - mean_squared_error: 0.0030 - root_

59/59 [==============================] - 0s 1ms/step - loss: 0.0181 - mean_squared_error: 0.0030 - root_mean_squared_error: 0.0546
Epoch 216/10000
59/59 [==============================] - 0s 950us/step - loss: 0.0184 - mean_squared_error: 0.0029 - root_mean_squared_error: 0.0540
Epoch 217/10000
59/59 [==============================] - 0s 925us/step - loss: 0.0185 - mean_squared_error: 0.0030 - root_mean_squared_error: 0.0547
Epoch 218/10000
59/59 [==============================] - 0s 950us/step - loss: 0.0182 - mean_squared_error: 0.0029 - root_mean_squared_error: 0.0541
Epoch 219/10000
59/59 [==============================] - 0s 1ms/step - loss: 0.0175 - mean_squared_error: 0.0029 - root_mean_squared_error: 0.0540
Epoch 220/10000
59/59 [==============================] - 0s 1ms/step - loss: 0.0180 - mean_squared_error: 0.0029 - root_mean_squared_error: 0.0539
Epoch 221/10000
59/59 [==============================] - 0s 1ms/step - loss: 0.0183 - mean_squared_error: 0.0030 - root_mean_squ

...

59/59 [==============================] - 0s 1ms/step - loss: 0.0087 - mean_squared_error: 2.1315e-04 - root_mean_squared_error: 0.0146
Epoch 5629/10000
59/59 [==============================] - 0s 889us/step - loss: 0.0085 - mean_squared_error: 2.0975e-04 - root_mean_squared_error: 0.0145
Epoch 5630/10000
59/59 [==============================] - 0s 795us/step - loss: 0.0084 - mean_squared_error: 2.0462e-04 - root_mean_squared_error: 0.0143
Epoch 5631/10000
59/59 [==============================] - 0s 1ms/step - loss: 0.0082 - mean_squared_error: 2.0129e-04 - root_mean_squared_error: 0.0142
Epoch 5632/10000
59/59 [==============================] - 0s 871us/step - loss: 0.0086 - mean_squared_error: 2.1036e-04 - root_mean_squared_error: 0.0145
Epoch 5633/10000
59/59 [==============================] - 0s 1ms/step - loss: 0.0086 - mean_squared_error: 2.1418e-04 - root_mean_squared_error: 0.0146
Epoch 5634/10000
59/59 [==============================] - 0s 939us/step - loss: 0.0083 - mean_squar

59/59 [==============================] - 0s 762us/step - loss: 0.0086 - mean_squared_error: 2.1717e-04 - root_mean_squared_error: 0.0147
Epoch 5682/10000
59/59 [==============================] - 0s 780us/step - loss: 0.0087 - mean_squared_error: 2.1496e-04 - root_mean_squared_error: 0.0147
Epoch 5683/10000
59/59 [==============================] - 0s 662us/step - loss: 0.0088 - mean_squared_error: 2.1856e-04 - root_mean_squared_error: 0.0148
Epoch 5684/10000
59/59 [==============================] - 0s 592us/step - loss: 0.0085 - mean_squared_error: 2.1210e-04 - root_mean_squared_error: 0.0146
Epoch 5685/10000
59/59 [==============================] - 0s 829us/step - loss: 0.0083 - mean_squared_error: 2.0596e-04 - root_mean_squared_error: 0.0144
Epoch 5686/10000
59/59 [==============================] - 0s 701us/step - loss: 0.0081 - mean_squared_error: 2.1386e-04 - root_mean_squared_error: 0.0146
Epoch 5687/10000
59/59 [==============================] - 0s 724us/step - loss: 0.0090 - mean

59/59 [==============================] - 0s 898us/step - loss: 0.0092 - mean_squared_error: 2.1715e-04 - root_mean_squared_error: 0.0147
Epoch 5735/10000
59/59 [==============================] - 0s 924us/step - loss: 0.0075 - mean_squared_error: 1.9414e-04 - root_mean_squared_error: 0.0139
Epoch 5736/10000
59/59 [==============================] - 0s 762us/step - loss: 0.0092 - mean_squared_error: 2.2786e-04 - root_mean_squared_error: 0.0151
Epoch 5737/10000
59/59 [==============================] - 0s 963us/step - loss: 0.0088 - mean_squared_error: 2.1878e-04 - root_mean_squared_error: 0.0148
Epoch 5738/10000
59/59 [==============================] - 0s 738us/step - loss: 0.0082 - mean_squared_error: 2.0953e-04 - root_mean_squared_error: 0.0145
Epoch 5739/10000
59/59 [==============================] - 0s 1ms/step - loss: 0.0089 - mean_squared_error: 2.1060e-04 - root_mean_squared_error: 0.0145
Epoch 5740/10000
59/59 [==============================] - 0s 934us/step - loss: 0.0089 - mean_s

59/59 [==============================] - 0s 667us/step - loss: 0.0082 - mean_squared_error: 2.0622e-04 - root_mean_squared_error: 0.0144
Epoch 5788/10000
59/59 [==============================] - 0s 883us/step - loss: 0.0084 - mean_squared_error: 2.1530e-04 - root_mean_squared_error: 0.0147
Epoch 5789/10000
59/59 [==============================] - 0s 911us/step - loss: 0.0087 - mean_squared_error: 2.1792e-04 - root_mean_squared_error: 0.0148
Epoch 5790/10000
59/59 [==============================] - 0s 775us/step - loss: 0.0085 - mean_squared_error: 2.0614e-04 - root_mean_squared_error: 0.0144
Epoch 5791/10000
59/59 [==============================] - 0s 1ms/step - loss: 0.0081 - mean_squared_error: 2.0107e-04 - root_mean_squared_error: 0.0142
Epoch 5792/10000
59/59 [==============================] - 0s 888us/step - loss: 0.0083 - mean_squared_error: 2.0552e-04 - root_mean_squared_error: 0.0143
Epoch 5793/10000
59/59 [==============================] - 0s 995us/step - loss: 0.0083 - mean_s

59/59 [==============================] - 0s 933us/step - loss: 0.0067 - mean_squared_error: 1.8861e-04 - root_mean_squared_error: 0.0137
Epoch 5841/10000
59/59 [==============================] - 0s 765us/step - loss: 0.0089 - mean_squared_error: 2.2248e-04 - root_mean_squared_error: 0.0149
Epoch 5842/10000
59/59 [==============================] - 0s 939us/step - loss: 0.0087 - mean_squared_error: 2.1222e-04 - root_mean_squared_error: 0.0146
Epoch 5843/10000
59/59 [==============================] - 0s 758us/step - loss: 0.0079 - mean_squared_error: 2.0036e-04 - root_mean_squared_error: 0.0142
Epoch 5844/10000
59/59 [==============================] - 0s 1ms/step - loss: 0.0086 - mean_squared_error: 2.1768e-04 - root_mean_squared_error: 0.0148
Epoch 5845/10000
59/59 [==============================] - 0s 892us/step - loss: 0.0076 - mean_squared_error: 1.9965e-04 - root_mean_squared_error: 0.0141
Epoch 5846/10000
59/59 [==============================] - 0s 1ms/step - loss: 0.0087 - mean_squ

# Loading of Model

In [4]:
'''Loads the Best Model Trained using Cross Validation'''
loaded_model = keras.models.load_model(f"Model\{directory_name}\model_{MAE.index(min(MAE)) + 1}")
print("Loaded model from disk")

'''Compilation of the model with its corresponding weights, followed by the evaluation of the model using test set'''
loaded_model.compile(loss = 'MeanAbsoluteError',\
                    optimizer = 'SGD',\
                    metrics = [tf.keras.metrics.MeanSquaredError(),\
                    tf.keras.metrics.RootMeanSquaredError()])

Loaded model from disk


# Visualisation of Predictions using Best Model from Cross Validation

In [5]:
'''Converting Categorical Data into binary representation'''
converted_visualise_dataset = convert_cat(dataset, cat_col, num_ori_feature, num_target, [dataset.iloc[:, 4].unique(), dataset.iloc[:, 5].unique()])

'''Feature Target Splitting'''
scaler = MinMaxScaler()
scaler.fit(converted_visualise_dataset)
normalised_dataset = pd.DataFrame(scaler.transform(converted_visualise_dataset), columns = get_col_names(converted_visualise_dataset))
feature, target = x_y_split(normalised_dataset, num_feature, num_target)
prediction = pd.DataFrame(loaded_model.predict(feature), columns = get_col_names(target))

'''Preparation to Rescale target values'''
min_y = dataset.iloc[:, num_ori_feature: num_ori_feature + num_target].min().to_list()
max_y = dataset.iloc[:, num_ori_feature: num_ori_feature + num_target].max().to_list()

corr_list = []
'''Tabulating the differences of Expected and Predictions made by the ANN Model'''
for i in range(len(feature)):
    '''Rescaling of normalised data'''
    expected = pd.DataFrame(inverse_transform(target.iloc[i].to_list(), max_y, min_y))
    predicted = pd.DataFrame(inverse_transform(prediction.iloc[i].to_list(), max_y, min_y))
    comparison_df = pd.concat([expected, predicted], axis = 1)
    comparison_df.columns = ['Expected', 'Predicted']
    comparison_df.index = get_col_names(target)
    display(comparison_df.style.set_caption(f"Element {i + 1}"))
    corr, _ = pearsonr(expected.iloc[:, 0].tolist(), predicted.iloc[:, 0].tolist())
    corr_list.append(corr)
    
'''Provide average score'''
print('------------------------------------------------------------------------')
print('Score per fold')
for i in range(0, len(corr_list)):
    print('------------------------------------------------------------------------')
    print(f'> Iteration {i+1} - Pearson Correlation: {corr_list[i]}') 
print('------------------------------------------------------------------------')
print('Average scores for all folds:')
print(f'> Average Pearsons Correlation: {np.mean(corr_list)} - Standard Deviation: {np.std(corr_list)}')
print('------------------------------------------------------------------------')  

------------------------------------------------------------------------
Score per fold
------------------------------------------------------------------------
> Iteration 1 - Pearson Correlation: 0.9999913117988821
------------------------------------------------------------------------
> Iteration 2 - Pearson Correlation: 0.9999882964714348
------------------------------------------------------------------------
> Iteration 3 - Pearson Correlation: 0.9999909359793977
------------------------------------------------------------------------
> Iteration 4 - Pearson Correlation: 0.9998785852515872
------------------------------------------------------------------------
> Iteration 5 - Pearson Correlation: 0.9999844218472153
------------------------------------------------------------------------
> Iteration 6 - Pearson Correlation: 0.9999905747890103
------------------------------------------------------------------------
> Iteration 7 - Pearson Correlation: 0.999987790623522
----------